# Wetterdaten

Als erstes müssen die Wetterdaten vom Wetterdienst heruntergeladen werden. Um die Daten vom OpenData Server herunterzuladen benutze ich BeautifulSoup zum Web Scraping.

Bevor BeautifulSoup benutzt werden kann muss ersteinmal der Inhalt der ersten Seiter heruntergeladen werden. Dazu wird mittels requests das HTML Dokument heruntergeladen.

In [1]:
from operator import contains
import requests
import os

import zipfile
import io
import pandas as pd

url = 'https://opendata.dwd.de/climate_environment/CDC/observations_germany/climate/10_minutes/air_temperature/now/'
download_folder = 'dwd-data/'

response = requests.get(url)
print(response)

<Response [200]>


Im nächsten Schritt wird dieses HTML dann analysiert. Um die Datein herunterzuladen wird jeder Link auf der dwd Webseite aus dem HTML Text gezogen. 

In [2]:
from bs4 import BeautifulSoup

soup = BeautifulSoup(response.text, 'html.parser')

dwd_links = soup.findAll('a')

print(dwd_links[2])

i = int(1)
dwd_len = len(dwd_links)

<a href="10minutenwerte_TU_00071_now.zip">10minutenwerte_TU_00071_now.zip</a>


Die so gefilterten Links werden dann in dieser Schleife heruntergeladen und gespeichert. Dazu wird noch ein Ordner angelegt in dem die Datein gespeichert werde können. Der pfad für die Stationsbeschreibungsdatei wird in eine extra Variable geschrieben um später damit zu arbeiten.

In [3]:
station_file = ''

for file_text in dwd_links:
    dwd_len = len(dwd_links)
    
    if (str(file_text.text).__contains__('10minutenwerte')):
        dest_file = download_folder + file_text.text
        if not os.path.isfile(dest_file):    
            file_url = url + "/" + file_text.text
            
            download(file_url, dest_file)
    elif (str(file_text)).__contains__('zehn_now_tu_Beschreibung_Stationen'):
        dest_file = download_folder + file_text.text
        file_url = url + "/" + file_text.text
        download(file_url,dest_file)
        station_file = dest_file
        
            
    print("Download ", i," von ",dwd_len, end='\r')
    i += 1
    
    def download(url, dest_file):
        response = requests.get(file_url)
        open(dest_file, 'wb').write(response.content)

Die Daten der Wetterstationen werden in die Klasse Station eingelesen. Aus den Klassen wird ein Dictionary erstellt in dem mittels der Stations_id gesucht werden kann. Weil die Stationsdaten nicht als csv gespeichert sind musste ich eine eigene Technik entwickeln um die Daten auszulesen.
Als erstes wird so lange gelesen bis kein Leerzeichen mehr erkannt wird. Danach wird gelesen bis wieder ein Leerzeichen erkannt wird. Dadurch können die Felder nacheinander eingelesen werden. 

In [33]:

class Station:
    def __init__(self, Stations_id, Stationshoehe,geoBreite, geoLaenge, Stationsname, Bundesland):
        self.Stations_id = Stations_id
        self.Stationshoehe = Stationshoehe
        self.geoBreite = geoBreite
        self.geoLaenge = geoLaenge
        self.name = Stationsname
        self.Bundesland = Bundesland

def read_station_file():
    
    def get_value(i,line):
        value = ""
        while(line[i] == ' '):
            i += 1
        while(line[i] != ' '):
            value += line[i]
            i += 1
        return (i,value)
    
    f = open(station_file, "r", encoding="1252")
    i = 0
    stations = {}
    for line in f:
        if i > 1:

            y = 0

            result = get_value(y,line)
            Stations_id = str(int(result[1])) #Die Konvertierung in int und zurück zu string entfernt die am Anfang leigenden nullen
            y = result[0]

            result = get_value(y,line)
            von_datum = result[1]
            y = result[0]

            result = get_value(y,line)
            bis_datum = result[1]
            y = result[0]

            result = get_value(y,line)
            Stationshoehe = result[1]
            y = result[0]

            result = get_value(y,line)
            geoBreite = result[1]
            y = result[0]

            result = get_value(y,line)
            geoLaenge = result[1]
            y = result[0]

            result = get_value(y,line)
            Stationsname = result[1]
            y = result[0]

            result = get_value(y,line)
            Bundesland = result[1]
            y = result[0]

            station = Station(Stations_id, Stationshoehe, geoBreite, geoLaenge, Stationsname ,Bundesland)
            stations[Stations_id] = station

        i+=1
    return(stations)

stations = read_station_file()
print(stations["73"].name)


Aldersbach-Kriestorf


Um an die Messerte in den Datein zu kommen müssen diese entpackt werden.

In [36]:
def read_dwd_file(file):
    df = pd.read_csv(file,sep=';')
    #print(df)
    #print(df.iat[0,1])
    #df.head()
    
for filename in os.listdir(download_folder):
    file_path = os.path.join(download_folder, filename)
    if(str(file_path).__contains__('.zip')):
        zip=zipfile.ZipFile(file_path)
        f=zip.open(zip.namelist()[0])
        read_dwd_file(f)
        #print(contents)
        
